In [2]:
from sklearn import datasets
from scipy.io.arff import loadarff
from sklearn.cross_validation import train_test_split
from sklearn.metrics import roc_auc_score

import numpy as np
import pandas as pd


In [3]:
forest = datasets.fetch_covtype()

In [4]:
type(forest)

sklearn.datasets.base.Bunch

In [5]:
X, X_test, y, y_test = train_test_split(
    forest.data, forest.target == 2, test_size=0.3, random_state=1234)

In [6]:
print(X.shape, y.shape, X_test.shape, y_test.shape)

(406708, 54) (406708,) (174304, 54) (174304,)


In [7]:
from sklearn import tree
clf = tree.DecisionTreeClassifier(min_samples_leaf=1000, min_samples_split=3000)

clf = clf.fit(X, y)

y_hat = clf.predict(X_test)

print("AUC = %.2f" % roc_auc_score(y_test, y_hat))

AUC = 0.79


In [8]:
from IPython.display import Image  
from sklearn.externals.six import StringIO  
import pydot_ng as pydot

%matplotlib inline

def plot_dtc(clf, features, classes):
    dot_data = StringIO()  
    tree.export_graphviz(clf, out_file=dot_data,  
                             feature_names=features,  
                             class_names=classes,  
                             filled=True, rounded=True,  
                             special_characters=True)  
    graph = pydot.graph_from_dot_data(dot_data.getvalue())  
    return Image(graph.create_png()) 
    
plot_dtc(clf, [str(i) for i in range(X.shape[1])], ["0","1"])

In [9]:
import random
from sklearn.tree import DecisionTreeClassifier
from sklearn.cross_validation import StratifiedKFold

paramgrid = {"max_features":      [4, "sqrt", 30, 40],
             "max_depth":         [10, 15, 20, 40, 50, 60],
             "min_samples_split": [100, 200, 500, 2000, 4000]
            }

random.seed(1)

from evolutionary_search import EvolutionaryAlgorithmSearchCV
cv = EvolutionaryAlgorithmSearchCV(estimator            =  DecisionTreeClassifier(),
                                   params               =  paramgrid,
                                   scoring              =  "roc_auc",
                                   cv                   =  StratifiedKFold(y, n_folds=4),
                                   verbose              = 1,
                                   population_size      = 10,
                                   gene_mutation_prob   = 0.2,
                                   gene_crossover_prob  = 0.5,
                                   tournament_size      = 5,
                                   generations_number   = 10,
                                   n_jobs=4)
%time cv.fit(X, y)

Types [1, 1, 1] and maxint [3, 5, 4] detected
--- Evolve in 120 possible combinations ---
gen	nevals	avg     	min     	max     
0  	10    	0.847246	0.706208	0.944029
1  	4     	0.914374	0.833362	0.944921
2  	10    	0.937796	0.869407	0.948001
3  	6     	0.946211	0.943621	0.948542
4  	4     	0.947715	0.944395	0.948542
5  	6     	0.946743	0.944105	0.948542
6  	6     	0.948278	0.944395	0.959198
7  	3     	0.954314	0.946708	0.959198
8  	0     	0.958999	0.957204	0.959198
9  	9     	0.956883	0.946708	0.959529
10 	8     	0.937368	0.867225	0.959529
Best individual is: {'max_features': 40, 'max_depth': 60, 'min_samples_split': 100}
with fitness: 0.959197991767
Scoring evaluations: 0, Cache hits: 0, Total: 0
CPU times: user 18.1 s, sys: 8.11 s, total: 26.2 s
Wall time: 2min 6s


In [10]:
clf = tree.DecisionTreeClassifier(min_samples_split=100, max_features=40, max_depth=50)

clf = clf.fit(X, y)

y_hat = clf.predict(X_test)

print("AUC = %.2f" % roc_auc_score(y_test, y_hat))

AUC = 0.90


In [11]:
importance = pd.DataFrame(
    {'imp': clf.tree_.compute_feature_importances(), 'f': range(X.shape[1])})
importance.sort_values(by="imp", ascending=False).head(10)

f       imp
0    0  0.391253
5    5  0.144509
9    9  0.130385
3    3  0.053278
4    4  0.034525
7    7  0.031541
1    1  0.019533
6    6  0.018251
8    8  0.015805
36  36  0.015160

In [12]:
clf = cv.best_estimator_
clf.fit(X,y)
print("AUC = %.2f" % roc_auc_score(y_test, clf.predict(X_test)))

AUC = 0.90


In [13]:
from sklearn.ensemble import RandomForestClassifier

rf = RandomForestClassifier(n_jobs = -1, n_estimators=400)

%time rf.fit(X,y)

print(roc_auc_score(y_test, rf.predict(X_test)))

CPU times: user 14min 35s, sys: 2.85 s, total: 14min 38s
Wall time: 3min 41s
0.961342826459


In [14]:
importance = pd.DataFrame(
    {'imp': rf.feature_importances_, 'f': range(X.shape[1])})
importance.sort_values(by="imp", ascending=False).head(10)

f       imp
0  0  0.247318
5  5  0.122112
9  9  0.113471
3  3  0.061760
4  4  0.058391
1  1  0.049099
7  7  0.045192
8  8  0.042089
6  6  0.040936
2  2  0.032708

In [15]:
from sklearn.ensemble import ExtraTreesClassifier

extra = ExtraTreesClassifier(n_jobs = -1, n_estimators=400)

%time extra.fit(X,y)

print(roc_auc_score(y_test, extra.predict(X_test)))

KeyboardInterrupt: 

In [ ]:
importance = pd.DataFrame(
    {'imp': extra.feature_importances_, 'f': range(X.shape[1])})
importance.sort_values(by="imp", ascending=False).head(10)

## Maintenant un peu de xgboost!

### D'abord sans deap

In [ ]:
import xgboost as xgb

dtrain = xgb.DMatrix(X, label=y)
dtest  = xgb.DMatrix(X_test, label=y_test)
evallist = [(dtest, 'eval'), (dtrain, 'train')]

param = {
    'bst:max_depth': 5, 
    'bst:eta': 0.5, 
    'silent': True, 
    'verbose': 0,
    'objective': 'binary:logistic',
    'nthread': 4,
    'eval_metric': 'auc'
}

num_round = 201
bst = xgb.train(param,
                dtrain,
                num_round,
                evallist,
                verbose_eval    = 40
               )


In [1]:
param = {
    'bst:max_depth': 9, 
    'bst:eta': 0.6,
    'colsample_bytree': 0.74,
    'subsample': 0.66,
    'silent': True, 
    'verbose': 0,
    'objective': 'binary:logistic',
    'nthread': 4,
    'eval_metric': 'auc'
}

num_round = 201
bst = xgb.train(param,
                dtrain,
                num_round,
                evallist,
                verbose_eval    = 40
               )


NameError: name 'xgb' is not defined

###  Ensuite avec deap

In [ ]:
import xgboost as xgb

import deapexp as dp

grid_gen1 = {
    "max_depth":          range(3, 11),
    "learning_rate":      np.logspace(-4, -1, 40, base=10),
    "subsample":          np.arange(0.5, 0.8, 2e-2),
    "colsample_bytree":   np.arange(0.1, 0.4, 2e-2)
}

genetic_params = {
    "generations_number": 10,
    "population_size": 30,
    "gene_mutation_prob": 0.2,
    "tournament_size": 3
}

num_rounds = 100

train = pd.DataFrame(X)
train["target"] = y

class IdentityTransformer(object):
    def __init__(*args, **kwargs):
        None
    def fit_transform(self, X):
        return X
    def transform(self, X):
        return X

e = dp.DEAPSplitXgboostExperiment(IdentityTransformer(),
                               grid_gen1,
                               test_prop=0.2,
                               genetic_params=genetic_params,
                               num_rounds=num_rounds)

e.experiment(train, "target")

Searching with train 325366 / test 81342
with params grid {'colsample_bytree': array([ 0.1 ,  0.12,  0.14,  0.16,  0.18,  0.2 ,  0.22,  0.24,  0.26,
        0.28,  0.3 ,  0.32,  0.34,  0.36,  0.38,  0.4 ]), 'max_depth': range(3, 11), 'learning_rate': array([ 0.0001    ,  0.00011938,  0.00014251,  0.00017013,  0.00020309,
        0.00024245,  0.00028943,  0.00034551,  0.00041246,  0.00049239,
        0.0005878 ,  0.0007017 ,  0.00083768,  0.001     ,  0.00119378,
        0.0014251 ,  0.00170125,  0.00203092,  0.00242446,  0.00289427,
        0.00345511,  0.00412463,  0.00492388,  0.00587802,  0.00701704,
        0.00837678,  0.01      ,  0.01193777,  0.01425103,  0.01701254,
        0.02030918,  0.02424462,  0.02894266,  0.03455107,  0.04124626,
        0.04923883,  0.05878016,  0.07017038,  0.08376776,  0.1       ]), 'subsample': array([ 0.5 ,  0.52,  0.54,  0.56,  0.58,  0.6 ,  0.62,  0.64,  0.66,
        0.68,  0.7 ,  0.72,  0.74,  0.76,  0.78,  0.8 ])}
on genetic params {'tournament

Types [2, 1, 2, 2] and maxint [15, 7, 39, 15] detected
--- Evolve in 81920 possible combinations ---
[CV] colsample_bytree=0.4, max_depth=7, learning_rate=0.00119377664171, subsample=0.62 
[CV]  colsample_bytree=0.4, max_depth=7, learning_rate=0.00119377664171, subsample=0.62, score=0.868058 -  13.6s
[CV] colsample_bytree=0.4, max_depth=6, learning_rate=0.0119377664171, subsample=0.78 
[CV]  colsample_bytree=0.4, max_depth=6, learning_rate=0.0119377664171, subsample=0.78, score=0.866245 -  13.7s
[CV] colsample_bytree=0.32, max_depth=6, learning_rate=0.020309176209, subsample=0.54 


In [24]:
(X.shape, y.shape)

((406708, 54), (406708,))